# NESS: Google Colab Tutorial

In [1]:
# install NESS Library

!pip install ness-search biopython pyMSA

# install MUSCLE

!apt install muscle ncbi-blast+

E: Could not open lock file /var/lib/dpkg/lock-frontend - open (13: Permission denied)
E: Unable to acquire the dpkg frontend lock (/var/lib/dpkg/lock-frontend), are you root?


In [2]:
from Bio import SeqIO
from Bio.Blast import NCBIXML
from IPython.display import HTML
from pymsa import MSA, Entropy, PercentageOfNonGaps, PercentageOfTotallyConservedColumns, Star, SumOfPairs
from pymsa import PAM250, Blosum62, FileMatrix
from pymsa.util.fasta import print_alignment
from scipy.stats import kruskal
from plotly import express as ex
import pandas as pd
import random
import os

## Downloading 

To ilustrate the usage of NESS, let's download a list of protein sequences from the Protein Data Bank (PDB) database.

In [3]:
!mkdir -p data/
!wget -O data/pdb_seqres.txt.gz https://files.wwpdb.org/pub/pdb/derived_data/pdb_seqres.txt.gz
!gzip -d -f data/pdb_seqres.txt.gz
!mv data/pdb_seqres.txt data/pdb_seqres.fasta

--2022-10-29 01:46:29--  https://files.wwpdb.org/pub/pdb/derived_data/pdb_seqres.txt.gz
Resolving files.wwpdb.org (files.wwpdb.org)... 128.6.158.70
Connecting to files.wwpdb.org (files.wwpdb.org)|128.6.158.70|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 42533197 (41M) [application/x-gzip]
Saving to: ‘data/pdb_seqres.txt.gz’

data/pdb_seqres.txt 100%[===================>]  40,56M  6,64MB/s    in 19s     

2022-10-29 01:46:49 (2,09 MB/s) - ‘data/pdb_seqres.txt.gz’ saved [42533197/42533197]



In [4]:
!head -10 data/pdb_seqres.fasta

>100d_A mol:na length:10  DNA/RNA (5'-R(*CP*)-D(*CP*GP*GP*CP*GP*CP*CP*GP*)-R(*G)-3')
CCGGCGCCGG
>100d_B mol:na length:10  DNA/RNA (5'-R(*CP*)-D(*CP*GP*GP*CP*GP*CP*CP*GP*)-R(*G)-3')
CCGGCGCCGG
>101d_A mol:na length:12  DNA (5'-D(*CP*GP*CP*GP*AP*AP*TP*TP*(CBR)P*GP*CP*G)-3')
CGCGAATTCGCG
>101d_B mol:na length:12  DNA (5'-D(*CP*GP*CP*GP*AP*AP*TP*TP*(CBR)P*GP*CP*G)-3')
CGCGAATTCGCG
>101m_A mol:protein length:154  MYOGLOBIN
MVLSEGEWQLVLHVWAKVEADVAGHGQDILIRLFKSHPETLEKFDRVKHLKTEAEMKASEDLKKHGVTVLTALGAILKKKGHHEAELKPLAQSHATKHKIPIKYLEFISEAIIHVLHSRHPGNFGADAQGAMNKALELFRKDIAAKYKELGYQG


As PDB also includes data from non-protein molecules (eg: DNA, RNA), let's filter only the protein sequences using the field `mol:protein` present in the FASTA header.

In [5]:
with open('data/pdb_seqres.fasta') as reader, open('data/pdb_seqres_proteins_only.fasta','w') as writer:
    for r, record in enumerate(SeqIO.parse(reader, 'fasta')):
        if 'mol:protein' in record.description:
            SeqIO.write([record], writer, 'fasta')

In [6]:
!head -10 data/pdb_seqres_proteins_only.fasta

>101m_A mol:protein length:154  MYOGLOBIN
MVLSEGEWQLVLHVWAKVEADVAGHGQDILIRLFKSHPETLEKFDRVKHLKTEAEMKASE
DLKKHGVTVLTALGAILKKKGHHEAELKPLAQSHATKHKIPIKYLEFISEAIIHVLHSRH
PGNFGADAQGAMNKALELFRKDIAAKYKELGYQG
>102l_A mol:protein length:165  T4 LYSOZYME
MNIFEMLRIDEGLRLKIYKDTEGYYTIGIGHLLTKSPSLNAAAKSELDKAIGRNTNGVIT
KDEAEKLFNQDVDAAVRGILRNAKLKPVYDSLDAVRRAALINMVFQMGETGVAGFTNSLR
MLQQKRWDEAAVNLAKSRWYNQTPNRAKRVITTFRTGTWDAYKNL
>102m_A mol:protein length:154  MYOGLOBIN
MVLSEGEWQLVLHVWAKVEADVAGHGQDILIRLFKSHPETLEKFDRFKHLKTEAEMKASE


## Creating sequence vectorization model

Now, we will create a protein sequence vectorization model based on the [Word2Vec algorithm](https://arxiv.org/abs/1301.3781). The model will be trained for `1 epoch` and considering a k-mer size with `k=5`. 

In [7]:
!ness build_model --help

usage: ness build_model [-h] --input INPUT --output OUTPUT
                        [--model-type {word2vec}] [--vector-size VECTOR_SIZE]
                        [--window-size WINDOW_SIZE] [--min-count MIN_COUNT]
                        [--ksize KSIZE] [--threads THREADS] [--epochs EPOCHS]
                        [--corpus-file CORPUS_FILE] [--both-strands] [--debug]

optional arguments:
  -h, --help            show this help message and exit
  --input INPUT         input file in FASTA format
  --output OUTPUT
  --model-type {word2vec}
  --vector-size VECTOR_SIZE
  --window-size WINDOW_SIZE
  --min-count MIN_COUNT
  --ksize KSIZE
  --threads THREADS
  --epochs EPOCHS
  --corpus-file CORPUS_FILE
  --both-strands
  --debug


In [8]:
!ness build_model \
  --input data/pdb_seqres_proteins_only.fasta \
  --ksize 5 \
  --epochs 10 \
  --output data/ness_pdb.model \
  --debug

 
       ▄▄    ▄ ▄▄▄▄▄▄▄ ▄▄▄▄▄▄▄ ▄▄▄▄▄▄▄ 
      █  █  █ █       █       █       █
      █   █▄█ █    ▄▄▄█  ▄▄▄▄▄█  ▄▄▄▄▄█
      █       █   █▄▄▄█ █▄▄▄▄▄█ █▄▄▄▄▄ 
      █  ▄    █    ▄▄▄█▄▄▄▄▄  █▄▄▄▄▄  █
      █ █ █   █   █▄▄▄ ▄▄▄▄▄█ █▄▄▄▄▄█ █
      █▄█  █▄▄█▄▄▄▄▄▄▄█▄▄▄▄▄▄▄█▄▄▄▄▄▄▄█      

Vector-based Alignment-free Sequence Search

2022-10-29 01:47:24,476 : INFO : Word2Vec lifecycle event {'params': 'Word2Vec<vocab=0, vector_size=100, alpha=0.025>', 'datetime': '2022-10-29T01:47:24.475699', 'gensim': '4.2.0', 'python': '3.7.12 | packaged by conda-forge | (default, Oct 26 2021, 06:08:53) \n[GCC 9.4.0]', 'platform': 'Linux-5.15.0-52-generic-x86_64-with-debian-bookworm-sid', 'event': 'created'}
2022-10-29 01:52:28,138 : INFO : collecting all words and their counts
2022-10-29 01:52:28,138 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2022-10-29 01:52:28,190 : INFO : PROGRESS: at sentence #1000, processed 205721 words, keeping 65766 word types
2022-10-29 01:52:2

2022-10-29 01:52:33,324 : INFO : PROGRESS: at sentence #65000, processed 15293528 words, keeping 1242119 word types
2022-10-29 01:52:33,396 : INFO : PROGRESS: at sentence #66000, processed 15513053 words, keeping 1251384 word types
2022-10-29 01:52:33,479 : INFO : PROGRESS: at sentence #67000, processed 15741008 words, keeping 1262075 word types
2022-10-29 01:52:33,561 : INFO : PROGRESS: at sentence #68000, processed 15993244 words, keeping 1270933 word types
2022-10-29 01:52:33,643 : INFO : PROGRESS: at sentence #69000, processed 16227910 words, keeping 1279759 word types
2022-10-29 01:52:33,723 : INFO : PROGRESS: at sentence #70000, processed 16464576 words, keeping 1290450 word types
2022-10-29 01:52:33,811 : INFO : PROGRESS: at sentence #71000, processed 16719866 words, keeping 1301259 word types
2022-10-29 01:52:33,889 : INFO : PROGRESS: at sentence #72000, processed 16963010 words, keeping 1307137 word types
2022-10-29 01:52:33,983 : INFO : PROGRESS: at sentence #73000, processed

2022-10-29 01:52:39,388 : INFO : PROGRESS: at sentence #136000, processed 32336832 words, keeping 1758653 word types
2022-10-29 01:52:39,467 : INFO : PROGRESS: at sentence #137000, processed 32583097 words, keeping 1763421 word types
2022-10-29 01:52:39,551 : INFO : PROGRESS: at sentence #138000, processed 32830442 words, keeping 1768176 word types
2022-10-29 01:52:39,635 : INFO : PROGRESS: at sentence #139000, processed 33107686 words, keeping 1772313 word types
2022-10-29 01:52:39,718 : INFO : PROGRESS: at sentence #140000, processed 33367722 words, keeping 1777971 word types
2022-10-29 01:52:39,813 : INFO : PROGRESS: at sentence #141000, processed 33638880 words, keeping 1783455 word types
2022-10-29 01:52:39,897 : INFO : PROGRESS: at sentence #142000, processed 33894033 words, keeping 1788358 word types
2022-10-29 01:52:39,984 : INFO : PROGRESS: at sentence #143000, processed 34137822 words, keeping 1794083 word types
2022-10-29 01:52:40,080 : INFO : PROGRESS: at sentence #144000, 

2022-10-29 01:52:46,030 : INFO : PROGRESS: at sentence #207000, processed 51295166 words, keeping 2028477 word types
2022-10-29 01:52:46,101 : INFO : PROGRESS: at sentence #208000, processed 51505058 words, keeping 2030141 word types
2022-10-29 01:52:46,243 : INFO : PROGRESS: at sentence #209000, processed 51813223 words, keeping 2033000 word types
2022-10-29 01:52:46,383 : INFO : PROGRESS: at sentence #210000, processed 52151820 words, keeping 2034918 word types
2022-10-29 01:52:46,496 : INFO : PROGRESS: at sentence #211000, processed 52433583 words, keeping 2037671 word types
2022-10-29 01:52:46,600 : INFO : PROGRESS: at sentence #212000, processed 52733106 words, keeping 2040843 word types
2022-10-29 01:52:46,703 : INFO : PROGRESS: at sentence #213000, processed 53016472 words, keeping 2043433 word types
2022-10-29 01:52:46,823 : INFO : PROGRESS: at sentence #214000, processed 53321998 words, keeping 2046460 word types
2022-10-29 01:52:46,910 : INFO : PROGRESS: at sentence #215000, 

2022-10-29 01:52:52,630 : INFO : PROGRESS: at sentence #278000, processed 69747999 words, keeping 2179017 word types
2022-10-29 01:52:52,710 : INFO : PROGRESS: at sentence #279000, processed 69971989 words, keeping 2180883 word types
2022-10-29 01:52:52,810 : INFO : PROGRESS: at sentence #280000, processed 70247014 words, keeping 2182347 word types
2022-10-29 01:52:52,928 : INFO : PROGRESS: at sentence #281000, processed 70559737 words, keeping 2184817 word types
2022-10-29 01:52:53,001 : INFO : PROGRESS: at sentence #282000, processed 70785045 words, keeping 2185546 word types
2022-10-29 01:52:53,073 : INFO : PROGRESS: at sentence #283000, processed 70964129 words, keeping 2186063 word types
2022-10-29 01:52:53,147 : INFO : PROGRESS: at sentence #284000, processed 71125989 words, keeping 2186294 word types
2022-10-29 01:52:53,198 : INFO : PROGRESS: at sentence #285000, processed 71263883 words, keeping 2186297 word types
2022-10-29 01:52:53,270 : INFO : PROGRESS: at sentence #286000, 

...

2022-10-29 15:33:55,822 : INFO : EPOCH 9 - PROGRESS: at 94.38% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:33:56,886 : INFO : EPOCH 9 - PROGRESS: at 94.40% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:33:57,978 : INFO : EPOCH 9 - PROGRESS: at 94.41% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:33:59,029 : INFO : EPOCH 9 - PROGRESS: at 94.42% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:34:00,073 : INFO : EPOCH 9 - PROGRESS: at 94.43% examples, 36390 words/s, in_qsize 8, out_qsize 0
2022-10-29 15:34:01,152 : INFO : EPOCH 9 - PROGRESS: at 94.45% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:34:02,210 : INFO : EPOCH 9 - PROGRESS: at 94.46% examples, 36390 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:34:03,389 : INFO : EPOCH 9 - PROGRESS: at 94.49% examples, 36391 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:34:04,411 : INFO : EPOCH 9 - PROGRESS: at 94.52% examples, 36394 words/s, in_qsize 7, out_

2022-10-29 15:35:17,758 : INFO : EPOCH 9 - PROGRESS: at 95.64% examples, 36392 words/s, in_qsize 8, out_qsize 0
2022-10-29 15:35:19,023 : INFO : EPOCH 9 - PROGRESS: at 95.66% examples, 36388 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:35:20,111 : INFO : EPOCH 9 - PROGRESS: at 95.70% examples, 36388 words/s, in_qsize 6, out_qsize 1
2022-10-29 15:35:21,113 : INFO : EPOCH 9 - PROGRESS: at 95.72% examples, 36389 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:35:22,168 : INFO : EPOCH 9 - PROGRESS: at 95.73% examples, 36389 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:35:23,414 : INFO : EPOCH 9 - PROGRESS: at 95.76% examples, 36388 words/s, in_qsize 8, out_qsize 0
2022-10-29 15:35:24,480 : INFO : EPOCH 9 - PROGRESS: at 95.77% examples, 36388 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:35:25,581 : INFO : EPOCH 9 - PROGRESS: at 95.79% examples, 36391 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:35:26,591 : INFO : EPOCH 9 - PROGRESS: at 95.79% examples, 36390 words/s, in_qsize 7, out_

2022-10-29 15:36:39,526 : INFO : EPOCH 9 - PROGRESS: at 96.82% examples, 36409 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:40,550 : INFO : EPOCH 9 - PROGRESS: at 96.85% examples, 36410 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:41,551 : INFO : EPOCH 9 - PROGRESS: at 96.88% examples, 36410 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:42,599 : INFO : EPOCH 9 - PROGRESS: at 96.90% examples, 36411 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:43,656 : INFO : EPOCH 9 - PROGRESS: at 96.92% examples, 36410 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:44,730 : INFO : EPOCH 9 - PROGRESS: at 96.93% examples, 36410 words/s, in_qsize 8, out_qsize 0
2022-10-29 15:36:45,773 : INFO : EPOCH 9 - PROGRESS: at 96.95% examples, 36411 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:46,778 : INFO : EPOCH 9 - PROGRESS: at 96.97% examples, 36411 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:36:47,880 : INFO : EPOCH 9 - PROGRESS: at 96.99% examples, 36415 words/s, in_qsize 7, out_

2022-10-29 15:38:00,702 : INFO : EPOCH 9 - PROGRESS: at 98.11% examples, 36428 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:01,726 : INFO : EPOCH 9 - PROGRESS: at 98.13% examples, 36429 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:02,758 : INFO : EPOCH 9 - PROGRESS: at 98.15% examples, 36429 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:03,793 : INFO : EPOCH 9 - PROGRESS: at 98.17% examples, 36429 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:04,863 : INFO : EPOCH 9 - PROGRESS: at 98.18% examples, 36429 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:06,304 : INFO : EPOCH 9 - PROGRESS: at 98.20% examples, 36428 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:07,347 : INFO : EPOCH 9 - PROGRESS: at 98.21% examples, 36428 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:08,369 : INFO : EPOCH 9 - PROGRESS: at 98.22% examples, 36428 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:38:09,414 : INFO : EPOCH 9 - PROGRESS: at 98.24% examples, 36429 words/s, in_qsize 7, out_

2022-10-29 15:39:22,940 : INFO : EPOCH 9 - PROGRESS: at 99.17% examples, 36419 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:23,993 : INFO : EPOCH 9 - PROGRESS: at 99.19% examples, 36419 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:25,136 : INFO : EPOCH 9 - PROGRESS: at 99.21% examples, 36419 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:26,164 : INFO : EPOCH 9 - PROGRESS: at 99.24% examples, 36419 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:27,168 : INFO : EPOCH 9 - PROGRESS: at 99.26% examples, 36418 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:28,206 : INFO : EPOCH 9 - PROGRESS: at 99.28% examples, 36418 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:29,277 : INFO : EPOCH 9 - PROGRESS: at 99.29% examples, 36418 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:30,321 : INFO : EPOCH 9 - PROGRESS: at 99.32% examples, 36418 words/s, in_qsize 7, out_qsize 0
2022-10-29 15:39:31,396 : INFO : EPOCH 9 - PROGRESS: at 99.34% examples, 36418 words/s, in_qsize 7, out_

## Creating sequence database

Based on the trained model, let's create a sequence database using the [ScaNN engine](https://arxiv.org/abs/1908.10396).

In [16]:
!ness build_database \
  --input data/pdb_seqres_proteins_only.fasta  \
  --model data/ness_pdb.model \
  --output data/ness_pdb.db \
  --debug

 
       ▄▄    ▄ ▄▄▄▄▄▄▄ ▄▄▄▄▄▄▄ ▄▄▄▄▄▄▄ 
      █  █  █ █       █       █       █
      █   █▄█ █    ▄▄▄█  ▄▄▄▄▄█  ▄▄▄▄▄█
      █       █   █▄▄▄█ █▄▄▄▄▄█ █▄▄▄▄▄ 
      █  ▄    █    ▄▄▄█▄▄▄▄▄  █▄▄▄▄▄  █
      █ █ █   █   █▄▄▄ ▄▄▄▄▄█ █▄▄▄▄▄█ █
      █▄█  █▄▄█▄▄▄▄▄▄▄█▄▄▄▄▄▄▄█▄▄▄▄▄▄▄█      

Vector-based Alignment-free Sequence Search

2022-10-30 13:45:18,421 : INFO : loading Word2Vec object from data/ness_pdb.model.vecs
2022-10-30 13:45:19,632 : INFO : loading wv recursively from data/ness_pdb.model.vecs.wv.* with mmap=None
2022-10-30 13:45:19,632 : INFO : loading vectors from data/ness_pdb.model.vecs.wv.vectors.npy with mmap=None
2022-10-30 13:45:19,882 : INFO : loading syn1neg from data/ness_pdb.model.vecs.syn1neg.npy with mmap=None
2022-10-30 13:45:20,596 : INFO : setting ignored attribute cum_table to None
2022-10-30 13:45:44,975 : INFO : Word2Vec lifecycle event {'fname': 'data/ness_pdb.model.vecs', 'datetime': '2022-10-30T13:45:44.974594', 'gensim': '4.2.0', 'python': '3.7.12 | pack

## Running a search against the database

With the formated database, we can compare a novel sequence to identify the most similar entries. To evaluate it, let's compare the protein sequence of the SARS-Cov-2 Spike protein and perform a multiple sequence alignment (MSA), comparing the results with those generated based on BLAST hits.

In [17]:
!wget -O data/spike.fasta https://rest.uniprot.org/uniprotkb/P0DTC2.fasta

--2022-10-30 13:56:03--  https://rest.uniprot.org/uniprotkb/P0DTC2.fasta
Resolving rest.uniprot.org (rest.uniprot.org)... failed: Temporary failure in name resolution.
wget: unable to resolve host address ‘rest.uniprot.org’


In [18]:
!cat data/spike.fasta 

In [19]:
%%time

!ness search \
  --input data/spike.fasta \
  --database data/ness_pdb.db \
  --output data/ness.csv \
  --hits 50

2022-10-30 13:56:38.143935: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-10-30 13:56:38.144028: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-10-30 13:56:50.132969: I scann/partitioning/partitioner_factory_base.cc:71] Size of sampled dataset for training partition: 99857
2022-10-30 13:56:54.229956: I ./scann/partitioning/kmeans_tree_partitioner_utils.h:102] PartitionerFactory ran in 4.046000386s.
CPU times: user 1.12 s, sys: 208 ms, total: 1.33 s
Wall time: 51.8 s


In [20]:
!cat data/ness.csv

cat: data/ness.csv: No such file or directory


In [21]:
df_ness_hits = pd.read_csv('data/ness.csv')
ness_hit_ids = list(df_ness_hits['subject'].head(50))

with open('data/ness_msa_inputs.fasta', 'w') as writer:
    for record in SeqIO.parse(open('data/spike.fasta'), 'fasta'):
        SeqIO.write([record], writer, 'fasta')
    for record in SeqIO.parse(open('data/pdb_seqres.fasta'), 'fasta'):
        if record.id in ness_hit_ids:
            SeqIO.write([record], writer, 'fasta')

FileNotFoundError: [Errno 2] No such file or directory: 'data/ness.csv'

In [ ]:
!muscle \
    -in data/ness_msa_inputs.fasta \
    -out data/ness_msa_output.fasta \
    -fasta

## Comparing top hits to BLAST

Now, let's compare the results obtained using NESS to those obtained using BLAST.

In [ ]:
!makeblastdb \
    -in data/pdb_seqres_proteins_only.fasta \
    -out data/pdb.blastdb \
    -dbtype prot

!blastp \
    -query data/spike.fasta \
    -db data/pdb.blastdb \
    -out data/blast.xml \
    -outfmt 5

Just like in the case of NESS, here we are going to select just to the top 10 results, as ranked by BLAST.

In [ ]:
blast_hits = NCBIXML.parse(open('data/blast.xml'))
blast_hits_ids = []
blast_hits_identity = []

for record in blast_hits:
    for alignment in record.alignments:
        blast_hits_ids.append(alignment.hit_def.split(' ')[0])
        blast_hits_identity.append(alignment.hsps[0].identities / alignment.hsps[0].align_length)
        if len(blast_hits_ids) == 50:
            break

with open('data/blast_msa_inputs.fasta', 'w') as writer:
    for record in SeqIO.parse(open('data/spike.fasta'), 'fasta'):
        SeqIO.write([record], writer, 'fasta')
        
    for record in SeqIO.parse(open('data/pdb_seqres.fasta'), 'fasta'):
        if record.id in blast_hits_ids:
            SeqIO.write([record], writer, 'fasta')

In [ ]:
len(blast_hits_ids)

In [ ]:
!muscle \
    -in data/blast_msa_inputs.fasta \
    -out data/blast_msa_output.fasta \
    -fasta 

The results generated by MUSCLE based on the hits detected by NESS and BLAST can be compared using the [AlignStat web server](http://alignstat.science.latrobe.edu.au/). From the PDB sequence dump obtained in October 20 (2022), the following report was generated. 

As we can see, the hits selected by NESS produced a better MSA when comparing to those selected by BLAST, probably because NESS considers an embedding representation of the sequence as a whole (global), instead of a sub-sequence of higher similarity (local), and uses a "semantically" representation that may also provide indirect information regarding the structure.


In [ ]:
def run_all_scores(sequences: list) -> None:
    
    aligned_sequences = list(pair[1] for pair in sequences)
    sequences_id = list(pair[0] for pair in sequences)

    msa = MSA(aligned_sequences, sequences_id)

    metrics = {
        'non_gaps': PercentageOfNonGaps(msa).compute(),
        'conserved': PercentageOfTotallyConservedColumns(msa).compute(),
        'entropy': Entropy(msa).compute(),
        'sum_of_pairs_blosum62': SumOfPairs(msa, Blosum62()).compute(),
        'sum_of_pairs_pam250': SumOfPairs(msa, PAM250()).compute(),
        'star_blosum62': Star(msa, Blosum62()).compute(),
        'star_pam250': Star(msa, PAM250()).compute(),
    }
    
    return metrics

In [ ]:
for fasta_file in ['data/ness_msa_output.fasta', 'data/blast_msa_output.fasta']:
    print(fasta_file)
    fasta_sequences = [(r.id, str(r.seq)) for r in SeqIO.parse(open(fasta_file), 'fasta')]
    print(run_all_scores(fasta_sequences))
    print('*'*100)